In [1]:
import tensorflow as tf
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

2024-04-27 11:51:55.928461: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-27 11:51:57.418145: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
#load dataset with redundant features removed (see NBA_predictive_model.ipynb)
df_NBA_slim = pd.read_csv('NBA_numeric_slim.csv')
df_NBA_slim.head()

season   age     w   sos  o_rtg  d_rtg  pace   f_tr  x3p_ar  ts_percent  \
0    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
1    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
2    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
3    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   
4    2005  26.0  13.0  0.09  100.6  111.1  91.4  0.299   0.146       0.504   

   ...  away_orb_percent  away_opp_e_fg_percent  away_opp_tov_percent  \
0  ...              27.2                  0.481                  14.2   
1  ...              29.5                  0.497                  14.7   
2  ...              28.4                  0.454                  14.4   
3  ...              28.4                  0.482                  15.1   
4  ...              31.2                  0.461                  13.5   

   away_opp_drb_percent  away_opp_ft_fga  away_attend  away_attend_g  \
0                  70.1            0.274     656081.0        16002.0   
1                  70.9            0.269     591701.0        14432.0   
2                  72.6            0.262     828384.0        20204.0   
3                  71.7            0.247     723949.0        17657.0   
4                  73.0            0.207     905116.0        22076.0   

   home_score  away_score  spread  
0         120         117       3  
1          90          93      -3  
2         105         114      -9  
3         110         107       3  
4          68          95     -27  

[5 rows x 38 columns]

In [3]:
#create training and test sets
train_set_r, test_val_set_r = train_test_split(df_NBA_slim, test_size=0.2, 
                                       stratify=df_NBA_slim['season'], random_state=42)

#separate into data (X) and targets(y).  Remove "season" and 'home_score' and 'away_score'
X_train_r = train_set_r.iloc[:,1:-3]
y_train_r = train_set_r.iloc[:,-1]

#split test_val_set into test and validation sets
test_set_r, val_set_r = train_test_split(test_val_set_r, test_size=0.5, 
                                       stratify=test_val_set_r['season'], random_state=42)

X_test_r = test_set_r.iloc[:,1:-3]
y_test_r = test_set_r.iloc[:,-1]

X_val_r = val_set_r.iloc[:,1:-3]
y_val_r = val_set_r.iloc[:,-1]

In [4]:
#z-score normalize the data
ss = StandardScaler()

X_train_r_ss = ss.fit_transform(X_train_r)
X_test_r_ss = ss.transform(X_test_r)
X_val_r_ss = ss.transform(X_val_r)

In [5]:
#define callback class
class Callback(tf.keras.callbacks.Callback):
    SHOW_NUMBER = 100
    counter = 0
    epoch = 0

    def on_epoch_begin(self, epoch, logs=None):
        self.epoch = epoch

    def on_epoch_end(self, batch, logs=None):
        if self.counter == self.SHOW_NUMBER or self.epoch == 1:
            print('Epoch: ' + str(self.epoch) + ' RMSE: ' + str(logs['RootMeanSquaredError']) + '   val_RMSE: ' +
                  str(logs['val_RootMeanSquaredError']))
            if self.epoch > 1:
                self.counter = 0
        self.counter += 1

In [5]:
#display shape of processed data
X_train_r_ss.shape


(9188, 34)

In [6]:
%%time

tf.random.set_seed(42)
model=tf.keras.Sequential([
    tf.keras.layers.Dense(100, input_shape=(34,), activation="relu"),
    tf.keras.layers.Dense(100, activation="relu"),
    tf.keras.layers.Dense(100, activation="relu"),
    tf.keras.layers.Dense(1,)
])
optimizer = tf.keras.optimizers.Adam(learning_rate=1e-3, weight_decay=1e-2)
model.compile(loss="mse", optimizer=optimizer, metrics=["RootMeanSquaredError"])

history = model.fit(X_train_r_ss, y_train_r, epochs=1000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/1000


/home/johann/miniconda3/envs/tensorflow/lib/python3.12/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
2024-04-25 15:03:18.711964: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-04-25 15:03:18.712418: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


288/288 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step - RootMeanSquaredError: 12.5365 - loss: 157.2030 - val_RootMeanSquaredError: 12.3262 - val_loss: 151.9363
Epoch 2/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 12.0827 - loss: 146.0708 - val_RootMeanSquaredError: 12.3137 - val_loss: 151.6277
Epoch 3/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 12.0212 - loss: 144.5828 - val_RootMeanSquaredError: 12.3222 - val_loss: 151.8358
Epoch 4/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 11.9700 - loss: 143.3503 - val_RootMeanSquaredError: 12.3425 - val_loss: 152.3370
Epoch 5/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 11.9165 - loss: 142.0686 - val_RootMeanSquaredError: 12.3632 - val_loss: 152.8493
Epoch 6/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 11.8526 - loss: 140.5461 - val_RootMeanSquaredError: 12.4183 - val_loss: 154.2148
Epoch 7/1000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step

In [7]:
#saving a model
model.save('long_train_model1.keras')

In [5]:
#try loading the model I just trained with this newer version of tensorflow
model = tf.keras.models.load_model('long_train_model1.keras')

2024-04-26 22:12:49.422012: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-04-26 22:12:49.422520: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [7]:
#nice!  That worked.  Train it some more to test.
history1 = model.fit(X_train_r_ss, y_train_r, epochs=100,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0)

In [8]:
#verbose2
history1 = model.fit(X_train_r_ss, y_train_r, epochs=100,
                    validation_data=(X_val_r_ss, y_val_r), verbose=2)

Epoch 1/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.7166 - loss: 2.9466 - val_RootMeanSquaredError: 15.3594 - val_loss: 235.9097
Epoch 2/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.7455 - loss: 3.0467 - val_RootMeanSquaredError: 15.2532 - val_loss: 232.6590
Epoch 3/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.6621 - loss: 2.7626 - val_RootMeanSquaredError: 15.2778 - val_loss: 233.4125
Epoch 4/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.6194 - loss: 2.6226 - val_RootMeanSquaredError: 15.2312 - val_loss: 231.9886
Epoch 5/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.7548 - loss: 3.0793 - val_RootMeanSquaredError: 15.2967 - val_loss: 233.9887
Epoch 6/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.8246 - loss: 3.3293 - val_RootMeanSquaredError: 15.2666 - val_loss: 233.0684
Epoch 7/100
288/288 - 0s - 1ms/step - RootMeanSquaredError: 1.8688 - loss: 3.4924 - val_RootMeanSquaredError: 15.2933 - val_loss: 233.8864
Epoch 8/100
288/288 - 0s - 

In [5]:
#define callback class
class Callback(tf.keras.callbacks.Callback):
    SHOW_NUMBER = 100
    counter = 0
    epoch = 0

    def on_epoch_begin(self, epoch, logs=None):
        self.epoch = epoch

    def on_epoch_end(self, batch, logs=None):
        if self.counter == self.SHOW_NUMBER or self.epoch == 1:
            print('Epoch: ' + str(self.epoch) + ' RMSE: ' + str(logs['RootMeanSquaredError']) + '   val_RMSE: ' +
                  str(logs['val_RootMeanSquaredError']))
            if self.epoch > 1:
                self.counter = 0
        self.counter += 1

In [7]:
history1 = model.fit(X_train_r_ss, y_train_r, epochs=60000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

Epoch: 1 RMSE: 1.6242824792861938   val_RMSE: 14.97269058227539
Epoch: 100 RMSE: 1.5446420907974243   val_RMSE: 15.043209075927734
Epoch: 200 RMSE: 1.514661431312561   val_RMSE: 15.082229614257812
Epoch: 300 RMSE: 1.663404107093811   val_RMSE: 14.987994194030762
Epoch: 400 RMSE: 1.5259071588516235   val_RMSE: 14.929145812988281
Epoch: 500 RMSE: 1.7846908569335938   val_RMSE: 15.061716079711914
Epoch: 600 RMSE: 1.613077998161316   val_RMSE: 14.90950870513916
Epoch: 700 RMSE: 1.606710433959961   val_RMSE: 14.953117370605469
Epoch: 800 RMSE: 1.6088049411773682   val_RMSE: 15.030359268188477
Epoch: 900 RMSE: 1.562395691871643   val_RMSE: 14.978997230529785
Epoch: 1000 RMSE: 1.7394193410873413   val_RMSE: 14.99864387512207
Epoch: 1100 RMSE: 1.6130262613296509   val_RMSE: 14.920028686523438
Epoch: 1200 RMSE: 1.5158129930496216   val_RMSE: 14.93812370300293
Epoch: 1300 RMSE: 1.5663584470748901   val_RMSE: 15.06656551361084
Epoch: 1400 RMSE: 1.5728299617767334   val_RMSE: 14.918838500976562
Ep

In [8]:
#saving the model again.  There was marginal improvement overnight.
#saving a model
model.save('long_train_model1.keras')

In [6]:
#load model
model = tf.keras.saving.load_model('long_train_model.keras')

In [7]:
history2 = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/10000


288/288 [==============================] - 2s 2ms/step - loss: 2.8866 - root_mean_squared_error: 1.6990 - val_loss: 223.1156 - val_root_mean_squared_error: 14.9371
Epoch 2/10000
288/288 [==============================] - 0s 2ms/step - loss: 3.2327 - root_mean_squared_error: 1.7980 - val_loss: 223.7756 - val_root_mean_squared_error: 14.9591
Epoch 3/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.7393 - root_mean_squared_error: 1.6551 - val_loss: 221.1037 - val_root_mean_squared_error: 14.8696
Epoch 4/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.5007 - root_mean_squared_error: 1.5814 - val_loss: 224.3921 - val_root_mean_squared_error: 14.9797
Epoch 5/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.2854 - root_mean_squared_error: 1.5118 - val_loss: 223.2944 - val_root_mean_squared_error: 14.9430
Epoch 6/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.2349 - root_mean_squared_erro

288/288 [==============================] - 1s 2ms/step - loss: 2.4017 - root_mean_squared_error: 1.5497 - val_loss: 223.9348 - val_root_mean_squared_error: 14.9645
Epoch 45/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.2071 - root_mean_squared_error: 1.4856 - val_loss: 223.9787 - val_root_mean_squared_error: 14.9659
Epoch 46/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.2479 - root_mean_squared_error: 1.4993 - val_loss: 222.9345 - val_root_mean_squared_error: 14.9310
Epoch 47/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.5727 - root_mean_squared_error: 1.6040 - val_loss: 224.1734 - val_root_mean_squared_error: 14.9724
Epoch 48/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.8813 - root_mean_squared_error: 1.6974 - val_loss: 226.8302 - val_root_mean_squared_error: 15.0609
Epoch 49/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.6800 - root_mean_squared_error: 1.6371 -

Epoch 90/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.8445 - root_mean_squared_error: 1.6866 - val_loss: 224.6455 - val_root_mean_squared_error: 14.9882
Epoch 91/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.8374 - root_mean_squared_error: 1.6845 - val_loss: 225.0819 - val_root_mean_squared_error: 15.0027
Epoch 92/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.4530 - root_mean_squared_error: 1.5662 - val_loss: 225.0412 - val_root_mean_squared_error: 15.0014
Epoch 93/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.6416 - root_mean_squared_error: 1.6253 - val_loss: 225.0660 - val_root_mean_squared_error: 15.0022
Epoch 94/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.8301 - root_mean_squared_error: 1.6823 - val_loss: 228.4265 - val_root_mean_squared_error: 15.1138
Epoch 95/10000
288/288 [==============================] - 0s 2ms/step - loss: 2.6434 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.6969 - root_mean_squared_error: 1.6422 - val_loss: 221.5972 - val_root_mean_squared_error: 14.8861
Epoch 136/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.9457 - root_mean_squared_error: 1.7163 - val_loss: 222.5245 - val_root_mean_squared_error: 14.9173
Epoch 137/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.0817 - root_mean_squared_error: 1.7555 - val_loss: 224.5993 - val_root_mean_squared_error: 14.9866
Epoch 138/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6751 - root_mean_squared_error: 1.6356 - val_loss: 223.5190 - val_root_mean_squared_error: 14.9506
Epoch 139/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6055 - root_mean_squared_error: 1.6142 - val_loss: 225.5389 - val_root_mean_squared_error: 15.0180
Epoch 140/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.1715 - root_mean_squared_error: 1.4

288/288 [==============================] - 1s 2ms/step - loss: 2.4289 - root_mean_squared_error: 1.5585 - val_loss: 224.2401 - val_root_mean_squared_error: 14.9746
Epoch 181/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3742 - root_mean_squared_error: 1.5408 - val_loss: 225.0001 - val_root_mean_squared_error: 15.0000
Epoch 182/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.5583 - root_mean_squared_error: 1.5995 - val_loss: 224.9358 - val_root_mean_squared_error: 14.9979
Epoch 183/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3369 - root_mean_squared_error: 1.5287 - val_loss: 220.8814 - val_root_mean_squared_error: 14.8621
Epoch 184/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4546 - root_mean_squared_error: 1.5667 - val_loss: 224.9416 - val_root_mean_squared_error: 14.9981
Epoch 185/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.7337 - root_mean_squared_error: 1.6

...

288/288 [==============================] - 1s 2ms/step - loss: 2.6630 - root_mean_squared_error: 1.6319 - val_loss: 223.5990 - val_root_mean_squared_error: 14.9532
Epoch 9811/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4911 - root_mean_squared_error: 1.5783 - val_loss: 227.7749 - val_root_mean_squared_error: 15.0922
Epoch 9812/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.8249 - root_mean_squared_error: 1.6807 - val_loss: 225.6345 - val_root_mean_squared_error: 15.0211
Epoch 9813/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.8882 - root_mean_squared_error: 1.6995 - val_loss: 226.4622 - val_root_mean_squared_error: 15.0487
Epoch 9814/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6976 - root_mean_squared_error: 1.6424 - val_loss: 223.9646 - val_root_mean_squared_error: 14.9654
Epoch 9815/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6385 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 2.6427 - root_mean_squared_error: 1.6256 - val_loss: 223.6357 - val_root_mean_squared_error: 14.9545
Epoch 9856/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.8120 - root_mean_squared_error: 1.6769 - val_loss: 226.7330 - val_root_mean_squared_error: 15.0577
Epoch 9857/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.7925 - root_mean_squared_error: 1.6711 - val_loss: 225.8251 - val_root_mean_squared_error: 15.0275
Epoch 9858/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4588 - root_mean_squared_error: 1.5681 - val_loss: 224.5998 - val_root_mean_squared_error: 14.9867
Epoch 9859/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.2880 - root_mean_squared_error: 1.5126 - val_loss: 223.7868 - val_root_mean_squared_error: 14.9595
Epoch 9860/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.1350 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 2.8900 - root_mean_squared_error: 1.7000 - val_loss: 224.4028 - val_root_mean_squared_error: 14.9801
Epoch 9901/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6559 - root_mean_squared_error: 1.6297 - val_loss: 225.7213 - val_root_mean_squared_error: 15.0240
Epoch 9902/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.6623 - root_mean_squared_error: 1.6317 - val_loss: 223.1677 - val_root_mean_squared_error: 14.9388
Epoch 9903/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4114 - root_mean_squared_error: 1.5529 - val_loss: 222.4194 - val_root_mean_squared_error: 14.9137
Epoch 9904/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.1351 - root_mean_squared_error: 1.4612 - val_loss: 228.1831 - val_root_mean_squared_error: 15.1057
Epoch 9905/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3530 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 2.7128 - root_mean_squared_error: 1.6471 - val_loss: 225.9882 - val_root_mean_squared_error: 15.0329
Epoch 9946/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.0905 - root_mean_squared_error: 1.7580 - val_loss: 223.2349 - val_root_mean_squared_error: 14.9410
Epoch 9947/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4658 - root_mean_squared_error: 1.5703 - val_loss: 224.3795 - val_root_mean_squared_error: 14.9793
Epoch 9948/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3248 - root_mean_squared_error: 1.5247 - val_loss: 224.5945 - val_root_mean_squared_error: 14.9865
Epoch 9949/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3971 - root_mean_squared_error: 1.5483 - val_loss: 223.4682 - val_root_mean_squared_error: 14.9489
Epoch 9950/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.7823 - root_mean_squared_error

288/288 [==============================] - 1s 2ms/step - loss: 2.9054 - root_mean_squared_error: 1.7045 - val_loss: 224.0732 - val_root_mean_squared_error: 14.9691
Epoch 9991/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.3474 - root_mean_squared_error: 1.5321 - val_loss: 226.0066 - val_root_mean_squared_error: 15.0335
Epoch 9992/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.1577 - root_mean_squared_error: 1.4689 - val_loss: 222.1189 - val_root_mean_squared_error: 14.9037
Epoch 9993/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.5615 - root_mean_squared_error: 1.6005 - val_loss: 227.6197 - val_root_mean_squared_error: 15.0871
Epoch 9994/10000
288/288 [==============================] - 1s 2ms/step - loss: 2.4810 - root_mean_squared_error: 1.5751 - val_loss: 224.8244 - val_root_mean_squared_error: 14.9941
Epoch 9995/10000
288/288 [==============================] - 1s 2ms/step - loss: 3.2613 - root_mean_squared_error

In [8]:
model.save('long_train_model.keras')

In [9]:
history3 = model.fit(X_train_r_ss, y_train_r, epochs=30000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.2456 - root_mean_squared_error: 1.4985 - val_loss: 219.5287 - val_root_mean_squared_error: 14.8165
Epoch 2/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.6050 - root_mean_squared_error: 1.6140 - val_loss: 223.6364 - val_root_mean_squared_error: 14.9545
Epoch 3/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.2155 - root_mean_squared_error: 1.7932 - val_loss: 221.5264 - val_root_mean_squared_error: 14.8838
Epoch 4/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.2308 - root_mean_squared_error: 1.7974 - val_loss: 223.5961 - val_root_mean_squared_error: 14.9531
Epoch 5/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.8025 - root_mean_squared_error: 1.6741 - val_loss: 225.8842 - val_root_mean_squared_error: 15.0294
Epoch 6/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.3843 - root_mean_squared_error:

Epoch 47/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.8699 - root_mean_squared_error: 1.6941 - val_loss: 222.3193 - val_root_mean_squared_error: 14.9104
Epoch 48/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.4632 - root_mean_squared_error: 1.5695 - val_loss: 221.3205 - val_root_mean_squared_error: 14.8768
Epoch 49/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.2823 - root_mean_squared_error: 1.5107 - val_loss: 222.6468 - val_root_mean_squared_error: 14.9214
Epoch 50/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.4101 - root_mean_squared_error: 1.5524 - val_loss: 222.9480 - val_root_mean_squared_error: 14.9314
Epoch 51/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.5712 - root_mean_squared_error: 1.6035 - val_loss: 223.4584 - val_root_mean_squared_error: 14.9485
Epoch 52/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.8305 - root_mean_squared_

Epoch 93/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.3946 - root_mean_squared_error: 1.5475 - val_loss: 223.1932 - val_root_mean_squared_error: 14.9397
Epoch 94/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.8019 - root_mean_squared_error: 1.6739 - val_loss: 221.2399 - val_root_mean_squared_error: 14.8741
Epoch 95/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.6826 - root_mean_squared_error: 1.6379 - val_loss: 221.8135 - val_root_mean_squared_error: 14.8934
Epoch 96/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.1589 - root_mean_squared_error: 1.4693 - val_loss: 224.0953 - val_root_mean_squared_error: 14.9698
Epoch 97/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.1734 - root_mean_squared_error: 1.4743 - val_loss: 226.2424 - val_root_mean_squared_error: 15.0414
Epoch 98/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.6122 - root_mean_squared_

288/288 [==============================] - 0s 2ms/step - loss: 2.7511 - root_mean_squared_error: 1.6586 - val_loss: 222.2601 - val_root_mean_squared_error: 14.9084
Epoch 139/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.4905 - root_mean_squared_error: 1.5781 - val_loss: 222.8019 - val_root_mean_squared_error: 14.9266
Epoch 140/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.8963 - root_mean_squared_error: 1.7018 - val_loss: 221.6753 - val_root_mean_squared_error: 14.8888
Epoch 141/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.9458 - root_mean_squared_error: 1.7163 - val_loss: 222.7813 - val_root_mean_squared_error: 14.9259
Epoch 142/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.5536 - root_mean_squared_error: 1.5980 - val_loss: 223.5111 - val_root_mean_squared_error: 14.9503
Epoch 143/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.6603 - root_mean_squared_error: 1.6

288/288 [==============================] - 0s 2ms/step - loss: 2.3843 - root_mean_squared_error: 1.5441 - val_loss: 224.0638 - val_root_mean_squared_error: 14.9688
Epoch 184/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.0106 - root_mean_squared_error: 1.7351 - val_loss: 226.6283 - val_root_mean_squared_error: 15.0542
Epoch 185/30000
288/288 [==============================] - 0s 2ms/step - loss: 3.1497 - root_mean_squared_error: 1.7747 - val_loss: 223.2518 - val_root_mean_squared_error: 14.9416
Epoch 186/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.7060 - root_mean_squared_error: 1.6450 - val_loss: 224.4639 - val_root_mean_squared_error: 14.9821
Epoch 187/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.5587 - root_mean_squared_error: 1.5996 - val_loss: 221.5843 - val_root_mean_squared_error: 14.8857
Epoch 188/30000
288/288 [==============================] - 0s 2ms/step - loss: 2.5714 - root_mean_squared_error: 1.6

...

288/288 [==============================] - 1s 2ms/step - loss: 2.2868 - root_mean_squared_error: 1.5122 - val_loss: 223.3769 - val_root_mean_squared_error: 14.9458
Epoch 29794/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.0650 - root_mean_squared_error: 1.4370 - val_loss: 222.4298 - val_root_mean_squared_error: 14.9141
Epoch 29795/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4099 - root_mean_squared_error: 1.5524 - val_loss: 222.0164 - val_root_mean_squared_error: 14.9002
Epoch 29796/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6311 - root_mean_squared_error: 1.6221 - val_loss: 223.5229 - val_root_mean_squared_error: 14.9507
Epoch 29797/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.9593 - root_mean_squared_error: 1.7203 - val_loss: 224.1717 - val_root_mean_squared_error: 14.9724
Epoch 29798/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7998 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.3094 - root_mean_squared_error: 1.5197 - val_loss: 221.3159 - val_root_mean_squared_error: 14.8767
Epoch 29839/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.3649 - root_mean_squared_error: 1.5378 - val_loss: 222.2046 - val_root_mean_squared_error: 14.9065
Epoch 29840/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.0305 - root_mean_squared_error: 1.7408 - val_loss: 222.4411 - val_root_mean_squared_error: 14.9145
Epoch 29841/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6743 - root_mean_squared_error: 1.6353 - val_loss: 222.8681 - val_root_mean_squared_error: 14.9288
Epoch 29842/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5486 - root_mean_squared_error: 1.5964 - val_loss: 221.8655 - val_root_mean_squared_error: 14.8952
Epoch 29843/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.2794 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.6079 - root_mean_squared_error: 1.6149 - val_loss: 220.4740 - val_root_mean_squared_error: 14.8484
Epoch 29884/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5158 - root_mean_squared_error: 1.5861 - val_loss: 220.6743 - val_root_mean_squared_error: 14.8551
Epoch 29885/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6029 - root_mean_squared_error: 1.6134 - val_loss: 221.6666 - val_root_mean_squared_error: 14.8885
Epoch 29886/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5444 - root_mean_squared_error: 1.5951 - val_loss: 220.1938 - val_root_mean_squared_error: 14.8389
Epoch 29887/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4753 - root_mean_squared_error: 1.5733 - val_loss: 221.6689 - val_root_mean_squared_error: 14.8885
Epoch 29888/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6085 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.4420 - root_mean_squared_error: 1.5627 - val_loss: 221.4326 - val_root_mean_squared_error: 14.8806
Epoch 29929/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.3879 - root_mean_squared_error: 1.5453 - val_loss: 224.2728 - val_root_mean_squared_error: 14.9757
Epoch 29930/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4556 - root_mean_squared_error: 1.5670 - val_loss: 225.1188 - val_root_mean_squared_error: 15.0040
Epoch 29931/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.6870 - root_mean_squared_error: 1.6392 - val_loss: 222.1660 - val_root_mean_squared_error: 14.9052
Epoch 29932/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.5346 - root_mean_squared_error: 1.5920 - val_loss: 218.3165 - val_root_mean_squared_error: 14.7755
Epoch 29933/30000
288/288 [==============================] - 1s 2ms/step - loss: 3.5095 - root_mean_squared_

288/288 [==============================] - 1s 2ms/step - loss: 2.3128 - root_mean_squared_error: 1.5208 - val_loss: 223.6726 - val_root_mean_squared_error: 14.9557
Epoch 29974/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.3286 - root_mean_squared_error: 1.5260 - val_loss: 221.6960 - val_root_mean_squared_error: 14.8895
Epoch 29975/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.2449 - root_mean_squared_error: 1.4983 - val_loss: 219.7913 - val_root_mean_squared_error: 14.8254
Epoch 29976/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.4071 - root_mean_squared_error: 1.5515 - val_loss: 222.3268 - val_root_mean_squared_error: 14.9106
Epoch 29977/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.3849 - root_mean_squared_error: 1.5443 - val_loss: 224.0865 - val_root_mean_squared_error: 14.9695
Epoch 29978/30000
288/288 [==============================] - 1s 2ms/step - loss: 2.7052 - root_mean_squared_

In [6]:
#load new machine model
model = tf.keras.models.load_model('long_train_model1.keras')

2024-04-27 10:18:23.596016: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-04-27 10:18:23.596547: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [6]:
#train some more
history3 = model.fit(X_train_r_ss, y_train_r, epochs=30000,
                    validation_data=(X_val_r_ss, y_val_r))

Epoch 1/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - RootMeanSquaredError: 3.1370 - loss: 9.8782 - val_RootMeanSquaredError: 15.4193 - val_loss: 237.7534
Epoch 2/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - RootMeanSquaredError: 2.4927 - loss: 6.2370 - val_RootMeanSquaredError: 15.5090 - val_loss: 240.5291
Epoch 3/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 1.8446 - loss: 3.4029 - val_RootMeanSquaredError: 15.5438 - val_loss: 241.6102
Epoch 4/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 1.5457 - loss: 2.3896 - val_RootMeanSquaredError: 15.4425 - val_loss: 238.4701
Epoch 5/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 1.4692 - loss: 2.1595 - val_RootMeanSquaredError: 15.4265 - val_loss: 237.9760
Epoch 6/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - RootMeanSquaredError: 1.5501 - loss: 2.4051 - val_RootMeanSquaredError: 15.5098 - val_loss: 240.5530
Epoch 7/30000
288/288 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/st

In [7]:
history1 = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

Epoch: 1 RMSE: 1.5800774097442627   val_RMSE: 14.824274063110352
Epoch: 100 RMSE: 1.5373703241348267   val_RMSE: 14.801918029785156
Epoch: 200 RMSE: 1.5562282800674438   val_RMSE: 14.828042030334473
Epoch: 300 RMSE: 1.5467631816864014   val_RMSE: 14.83452033996582
Epoch: 400 RMSE: 1.5861396789550781   val_RMSE: 14.882051467895508
Epoch: 500 RMSE: 1.4956332445144653   val_RMSE: 14.840570449829102
Epoch: 600 RMSE: 1.461138367652893   val_RMSE: 14.837003707885742
Epoch: 700 RMSE: 1.6205333471298218   val_RMSE: 14.839659690856934
Epoch: 800 RMSE: 1.5416009426116943   val_RMSE: 14.852697372436523
Epoch: 900 RMSE: 1.4702709913253784   val_RMSE: 14.795900344848633
Epoch: 1000 RMSE: 1.4085139036178589   val_RMSE: 14.7589111328125
Epoch: 1100 RMSE: 1.4011446237564087   val_RMSE: 14.835660934448242
Epoch: 1200 RMSE: 1.4150257110595703   val_RMSE: 14.833771705627441
Epoch: 1300 RMSE: 1.5318610668182373   val_RMSE: 14.856267929077148
Epoch: 1400 RMSE: 1.6477980613708496   val_RMSE: 14.919353485107

In [8]:
#save the model 042724
model.save('long_train_model1.keras')

In [9]:
#train some more
history2 = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

#found cat sitting on keyboard (locked keyboard).  Process had stopped.  I blame the cat although I'm
#not sure how she got through the locked keyboard.  Machine wouldn't wake up, so I had to reboot.

Epoch: 1 RMSE: 1.5709000825881958   val_RMSE: 14.707215309143066
Epoch: 100 RMSE: 1.3832306861877441   val_RMSE: 14.776260375976562
Epoch: 200 RMSE: 1.4938533306121826   val_RMSE: 14.771430015563965
Epoch: 300 RMSE: 1.7031762599945068   val_RMSE: 14.808884620666504
Epoch: 400 RMSE: 1.3912087678909302   val_RMSE: 14.668614387512207
Epoch: 500 RMSE: 1.5640714168548584   val_RMSE: 14.680522918701172
Epoch: 600 RMSE: 1.4161982536315918   val_RMSE: 14.728006362915039
Epoch: 700 RMSE: 1.6481478214263916   val_RMSE: 14.650914192199707
Epoch: 800 RMSE: 1.5396027565002441   val_RMSE: 14.579195022583008
Epoch: 900 RMSE: 1.5771067142486572   val_RMSE: 14.775636672973633
Epoch: 1000 RMSE: 1.5178329944610596   val_RMSE: 14.719122886657715
Epoch: 1100 RMSE: 1.4312784671783447   val_RMSE: 14.765531539916992
Epoch: 1200 RMSE: 1.450568437576294   val_RMSE: 14.704773902893066


In [6]:
#load the model
model = tf.keras.models.load_model('long_train_model1.keras')

2024-04-27 11:55:36.564890: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-04-27 11:55:36.565289: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [7]:
#train the model 
history = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

Epoch: 1 RMSE: 1.508315920829773   val_RMSE: 14.769006729125977
Epoch: 100 RMSE: 1.4233943223953247   val_RMSE: 14.72118854522705
Epoch: 200 RMSE: 1.4955682754516602   val_RMSE: 14.772822380065918
Epoch: 300 RMSE: 1.4625144004821777   val_RMSE: 14.760218620300293
Epoch: 400 RMSE: 1.5412758588790894   val_RMSE: 14.742759704589844
Epoch: 500 RMSE: 1.5865678787231445   val_RMSE: 14.612011909484863
Epoch: 600 RMSE: 1.4753260612487793   val_RMSE: 14.744773864746094
Epoch: 700 RMSE: 1.438984990119934   val_RMSE: 14.659674644470215
Epoch: 800 RMSE: 1.6021305322647095   val_RMSE: 14.74862003326416
Epoch: 900 RMSE: 1.4428541660308838   val_RMSE: 14.810694694519043
Epoch: 1000 RMSE: 1.4843741655349731   val_RMSE: 14.702787399291992
Epoch: 1100 RMSE: 1.4185364246368408   val_RMSE: 14.688232421875
Epoch: 1200 RMSE: 1.477002739906311   val_RMSE: 14.732586860656738
Epoch: 1300 RMSE: 1.5599266290664673   val_RMSE: 14.683502197265625
Epoch: 1400 RMSE: 1.3869441747665405   val_RMSE: 14.634000778198242


In [8]:
#save the model 042724
model.save('long_train_model1.keras')

In [9]:
#train the model 
history = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

Epoch: 1 RMSE: 1.4633350372314453   val_RMSE: 14.764288902282715
Epoch: 100 RMSE: 1.4949513673782349   val_RMSE: 14.681674003601074
Epoch: 200 RMSE: 1.4379526376724243   val_RMSE: 14.832221984863281
Epoch: 300 RMSE: 1.5277788639068604   val_RMSE: 14.729043006896973
Epoch: 400 RMSE: 1.365545392036438   val_RMSE: 14.752620697021484
Epoch: 500 RMSE: 1.5903408527374268   val_RMSE: 14.78089714050293
Epoch: 600 RMSE: 1.463071346282959   val_RMSE: 14.765517234802246
Epoch: 700 RMSE: 1.5207802057266235   val_RMSE: 14.761425018310547
Epoch: 800 RMSE: 1.411470651626587   val_RMSE: 14.733491897583008
Epoch: 900 RMSE: 1.6030895709991455   val_RMSE: 14.641744613647461
Epoch: 1000 RMSE: 1.5296658277511597   val_RMSE: 14.744997024536133
Epoch: 1100 RMSE: 1.4150534868240356   val_RMSE: 14.67846965789795
Epoch: 1200 RMSE: 1.7108042240142822   val_RMSE: 14.70464038848877
Epoch: 1300 RMSE: 1.5098212957382202   val_RMSE: 14.659673690795898
Epoch: 1400 RMSE: 1.467789888381958   val_RMSE: 14.659513473510742

In [10]:
#save the model 042724
model.save('long_train_model1.keras')

In [11]:
#train the model 
history = model.fit(X_train_r_ss, y_train_r, epochs=10000,
                    validation_data=(X_val_r_ss, y_val_r), verbose=0, callbacks=[Callback()])

Epoch: 1 RMSE: 1.597596526145935   val_RMSE: 14.585502624511719
Epoch: 100 RMSE: 1.674461841583252   val_RMSE: 14.581093788146973
Epoch: 200 RMSE: 1.560413122177124   val_RMSE: 14.651690483093262
Epoch: 300 RMSE: 1.5193872451782227   val_RMSE: 14.718486785888672
Epoch: 400 RMSE: 1.4283397197723389   val_RMSE: 14.656201362609863
Epoch: 500 RMSE: 1.3053430318832397   val_RMSE: 14.624211311340332
Epoch: 600 RMSE: 1.545143485069275   val_RMSE: 14.660436630249023
Epoch: 700 RMSE: 1.4126720428466797   val_RMSE: 14.645462036132812
Epoch: 800 RMSE: 1.4393242597579956   val_RMSE: 14.6564359664917
Epoch: 900 RMSE: 1.7663817405700684   val_RMSE: 14.75944709777832
Epoch: 1000 RMSE: 1.4822646379470825   val_RMSE: 14.827681541442871
Epoch: 1100 RMSE: 1.4094716310501099   val_RMSE: 14.642013549804688
Epoch: 1200 RMSE: 1.4920352697372437   val_RMSE: 14.712390899658203
Epoch: 1300 RMSE: 1.5193347930908203   val_RMSE: 14.73488998413086
Epoch: 1400 RMSE: 1.4002124071121216   val_RMSE: 14.646466255187988


In [12]:
#save the model 042724
model.save('long_train_model1.keras')